In [30]:
from bs4 import BeautifulSoup
import pprint as pp
import pandas as pd
import matplotlib.pyplot as plt
from decimal import Decimal
import time
from datetime import datetime
from datetime import date
pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows', 500)
import pickle

In [31]:
listXML = open("userAnime/my_anime_list.xml", "r", encoding="utf8").read()
listXML = listXML.replace("\t", "").replace("\n","")
soup = BeautifulSoup(listXML)
myinfo = {}
for i in soup.myanimelist.myinfo:
    try:
        if i.name not in ['user_name']:
            myinfo[i.name] = int(i.text)
        else:
            myinfo[i.name] = i.text
    except Exception as e:
        #print(f"{e} -> {i.text}")
        pass
        
pp.pprint(myinfo)

animes = []
for anime in soup.find_all('anime'):
    animeAttrs = {}
    for attr in anime:
        if attr.name in ["my_finish_date", "my_rewatch_value", "my_start_date", "my_id", "my_rated",
                        "my_rewatching_ep", "my_tags", "my_storage", "series_title",
                        "my_dvd", "my_comments", "update_on_import", "my_rewatching", 
                        ]:
            continue
        try:
            animeAttrs[attr.name] = int(attr.text)
        except:
            animeAttrs[attr.name] = attr.text
    animes.append(animeAttrs)
len(animes)

{'user_export_type': 1,
 'user_id': 4957104,
 'user_name': 'mcrider',
 'user_total_anime': 1315,
 'user_total_completed': 563,
 'user_total_dropped': 4,
 'user_total_onhold': 90,
 'user_total_plantowatch': 585,
 'user_total_watching': 73}


1315

In [32]:
soup.myanimelist.myinfo.user_total_completed.string

'563'

In [53]:
def prepareMALdf(MALAnimeFile):
    df = pd.read_csv(MALAnimeFile)
    df = df.rename(index=str, columns={"animeID": "series_animedb_id"})
    df.set_index("series_animedb_id", inplace=True)
    for k in df.keys():
        df = df.rename(columns={k: k.strip()})
    return df

def filldfna(df):
    nulls = dict(df.isnull().sum())
    for i in nulls:
        if nulls[i] > 0:
            if i not in df.select_dtypes(['float64','int64']).keys():
                df = df.fillna(value={i:""})
            else:
                df = df.fillna(value={i:-1})
    return df

def preparePandas(animes):
    start_time = time.time()
    MAL_df = prepareMALdf("Anime.csv")
    
    episode_nums = []   
    for i in MAL_df["episodes"]:
        try:
            i = int(i)
        except:
            i = -1
        if i < 12: # OVA or unknown
            episode_nums.append(0)
        elif i >=12 and i < 20: # standard length
            episode_nums.append(1)
        elif i >=20 and i<30: # cour
            episode_nums.append(2)
        elif i>=30 and i<100: # extended
            episode_nums.append(3)
        elif i>=100: # franchise
            episode_nums.append(4)

    MAL_df["length_type"]=episode_nums

    # prepare genres
    genres=[]
    for i in MAL_df["genre"].unique().tolist():
        try:
            i = eval(i)
        except:
            continue
        for k in i:
            if k not in genres:
                genres.append(k)
    length_types = ["OVA","standard", "cour","extended","franchise"]
    genres_dict={}
    for g in genres:
        genre_def=[]
        for i in MAL_df["genre"]:
            try:
                i = eval(i)
            except:
                i = []
            if g in i:
                genre_def.append(1)
            else:
                genre_def.append(0)
        genres_dict[g] = genre_def
    for i in genres_dict:
        MAL_df[i] = genres_dict[i]

    unique_col_elem_list={}   
    for f in ["source", "type", "rating", "duration"]:
        unique_col_elem_list[f"{f}s_list"] = MAL_df[f].unique().tolist()
        elems=[]
        for i in MAL_df[f]:
            elems.append(unique_col_elem_list[f"{f}s_list"].index(i))
        MAL_df[f] = elems

    year_diff=[]
    for i in MAL_df["aired"]:
        try:
            startYear = eval(i)["prop"]["from"]["year"]
        except Exception as e:
            startYear = None
        #startMonth = eval(i)["prop"]["from"]["month"]
        #startDay = eval(i)["prop"]["from"]["day"]    
        #StartDate = [startYear, startMonth, startDay]
        try:
            year_diff.append(startYear-datetime.today().year)
        except Exception as e:
            #print(f"{e} -> {i}")
            year_diff.append(-1)
    len(year_diff)
    MAL_df["year_diff"] = year_diff
    del year_diff

    MAL_df = MAL_df[MAL_df["Hentai"]!=1]
        
    MAL_df = filldfna(MAL_df)
    
    myAnime_df = pd.DataFrame(data=animes)
    myAnime_df = filldfna(myAnime_df)
    myAnime_df.set_index("series_animedb_id", inplace=True)
    myAnime_df = myAnime_df.sort_values("series_animedb_id")
    myAnime_df = pd.merge(myAnime_df, MAL_df, on='series_animedb_id')
    myAnime_df = myAnime_df[myAnime_df["Hentai"]!=1]
    myAnime_df.to_pickle(f"userAnime/my-anime-df-{len(myAnime_df)}-LEN.pkl")
    statuses_keys = {"preddfCols":{"my_status": myAnime_df["my_status"],
                                  "my_times_watched": myAnime_df["my_times_watched"],
                                  "my_watched_episodes":myAnime_df["my_watched_episodes"]},
    "keys": myAnime_df["my_status"].index.tolist()}
    myAnime_df = myAnime_df.drop(["title_english", "title_japanese", "synopsis", "series_type",
                                  "background", "related", "genre", "studio", "producers", "broadcast",
                                 "airing", "aired", "title_synonyms", "my_watched_episodes", "series_episodes",
                                 "my_status", "my_times_watched", "name", "premiered", "episodes", "Hentai", "status"], axis=1)
    myAnime_df=myAnime_df.dropna()
    #myAnime_df["score_diff"] = myAnime_df["my_score"] - myAnime_df["score"]
    print(f">>> done parsing anime and cleaning, it took {round(time.time()-start_time, 2)}s")
    print(f">>> Their are {len(myAnime_df.keys())} keys")
    
    MAL_df = MAL_df.drop(columns=["duration", "Hentai", "episodes"])
    return myAnime_df, MAL_df.select_dtypes(['float64','int64']), statuses_keys

myAnime_df, MAL_df, statuses_keys = preparePandas(animes)
myAnime_df.keys()

>>> done parsing anime and cleaning, it took 6.46s
>>> Their are 55 keys


Index(['my_score', 'type', 'source', 'duration', 'rating', 'score',
       'scored_by', 'rank', 'popularity', 'members', 'favorites',
       'length_type', 'Action', 'Adventure', 'Comedy', 'Drama', 'Sci-Fi',
       'Space', 'Mystery', 'Shounen', 'Magic', 'Police', 'Supernatural',
       'Fantasy', 'Josei', 'Romance', 'Slice of Life', 'Sports', 'Cars',
       'Seinen', 'Horror', 'Psychological', 'Thriller', 'Super Power',
       'Martial Arts', 'School', 'Ecchi', 'Vampire', 'Military', 'Historical',
       'Dementia', 'Mecha', 'Demons', 'Samurai', 'Game', 'Shoujo', 'Harem',
       'Music', 'Shoujo Ai', 'Shounen Ai', 'Kids', 'Parody', 'Yuri', 'Yaoi',
       'year_diff'],
      dtype='object')

In [34]:
MAL_df.isnull().sum()
len(myAnime_df)

1270

In [35]:
myAnime_df[myAnime_df["my_score"]>0]

my_score  type  source  duration  rating  score  scored_by  \
series_animedb_id                                                               
1                         8     0       0         0       0   8.81   405664.0   
6                         7     0       1         0       1   8.30   212537.0   
30                        7     0       0         0       1   8.33   402215.0   
50                        8     0       1         0       1   7.42    59169.0   
79                        6     0       4         3       3   7.21   101261.0   
101                       8     0       4         0       1   7.41   120702.0   
122                       7     0       1         0       1   8.04    32470.0   
157                       7     0       1         3       1   7.06    47384.0   
189                       8     0       1         3       1   7.23   104267.0   
199                      10     1       0        29       2   8.91   550969.0   
226                       5     0       1         2       3   7.72   549257.0   
227                       7     2       0         2       1   8.07   252437.0   
276                       8     0       1         0       3   7.25    20564.0   
330                       8     0       1         0       3   7.38    64075.0   
343                       7     0       1         0       1   7.09    21830.0   
355                       9     0       2         0       1   7.63   190060.0   
357                       7     2       2         2       0   6.73    83658.0   
382                       5     2       1        26       3   6.47    13103.0   
384                       5     0       1         6       3   7.17   116369.0   
390                       7     0       1         3       1   7.31    41093.0   
412                       7     0       1         0       3   6.63    32523.0   
469                       9     0       1         3       1   7.27    68637.0   
482                       8     0       1         3       1   7.23    65845.0   
509                       6     0       0         2       1   6.88    15751.0   
587                       8     0       2         0       1   7.61    39958.0   
777                       9     2       1       107       0   8.51   243692.0   
849                       7     0       2         3       1   7.97   322527.0   
853                       8     0       1         3       1   8.32   354874.0   
880                       7     0       1         0       1   7.65    27626.0   
889                       9     0       1         0       0   8.12   251420.0   
910                       8     0       0         0       1   6.40     5954.0   
918                       7     0       1         0       1   9.00   155333.0   
940                       6     0       2         3       1   7.34    23583.0   
1066                      5     3       6        88       1   7.18    16098.0   
1067                      8     0       4         2       0   6.64    10906.0   
1195                      8     0       2         3       1   7.51   292437.0   
1210                      9     0       5         0       3   8.37   202628.0   
1250                      7     0       1         0       1   7.38    35622.0   
1519                      8     0       1         0       0   8.25   176872.0   
1546                      8     0       1         3       1   7.13    24365.0   
1568                      7     0       1         0       1   7.01    17351.0   
1569                      7     0       4         0       1   7.13    21566.0   
1575                     10     0       0         0       0   8.77   681621.0   
1581                      6     0       4         0       1   6.72    11364.0   
1689                      8     1       0         6       1   7.91   303519.0   
1691                      8     0       2         0       1   7.42   154407.0   
1698                      8     0       1         6       1   8.39    92020.0   
1721                      7     0       1         

In [36]:
MAL_df.dtypes
MAL_df.select_dtypes(['float64','int64'])
print(len(MAL_df))
MAL_df

14039


type  source  rating  score  scored_by     rank  \
series_animedb_id                                                    
1                     0       0       0   8.81   405664.0     26.0   
5                     1       0       0   8.41   120243.0    164.0   
6                     0       1       1   8.30   212537.0    255.0   
7                     0       0       1   7.33    32837.0   2371.0   
8                     0       1       2   7.03     4894.0   3544.0   
16                    0       1       1   8.12    57065.0    419.0   
17                    0       1       1   7.67     9307.0   1186.0   
18                    0       1       1   8.23    42555.0    298.0   
19                    0       1       3   8.69   131233.0     49.0   
20                    0       1       1   7.90   716412.0    705.0   
21                    0       1       1   8.53   465454.0     94.0   
22                    0       1       1   8.00    50306.0    577.0   
23                    0       1       2   6.54      825.0   5641.0   
25                    0       1       0   7.50    36185.0   1679.0   
26                    0       0       3   7.78    32198.0    942.0   
27                    0       2       0   7.40    61471.0   2081.0   
28                    0       1       1   8.01    27616.0    566.0   
29                    0       1       1   7.54     4534.0   1564.0   
30                    0       0       1   8.33   402215.0    215.0   
31                    1       0       0   7.50    74480.0   1672.0   
32                    1       0       3   8.50   215979.0    107.0   
33                    0       1       3   8.47   166504.0    124.0   
43                    1       1       3   8.34   199591.0    209.0   
44                    2       1       0   8.78    94681.0     31.0   
45                    0       1       1   8.39   143693.0    182.0   
46                    1       1       0   7.62    21576.0   1325.0   
47                    1       1       3   8.17   214961.0    356.0   
48                    0       0       1   7.08    63557.0   3341.0   
50                    0       1       1   7.42    59169.0   1949.0   
51                    2       1       3   6.40    23620.0   6216.0   
53                    0       1       1   7.20    40592.0   2844.0   
54                    1       1       0   7.18    34723.0   2935.0   
55                    0       3       0   6.59     4474.0   5373.0   
56                    0       0       0   5.96     5451.0   7805.0   
57                    0       1       0   8.36    91614.0    197.0   
58                    0       0       3   7.11    21542.0   3232.0   
59                    0       1       1   7.51   182381.0   1629.0   
60                    0       1       0   7.75    81366.0    985.0   
61                    0       1       1   7.30    78088.0   2456.0   
62                    0       4       1   6.86    24731.0   4164.0   
63                    0       1       3   6.73    61303.0   4750.0   
64                    0       1       1   7.52    76580.0   1617.0   
65                    0       1       1   7.73    48438.0   1053.0   
67                    0       1       0   7.64    57199.0   1249.0   
69                    0       0       1   6.44     2241.0   6013.0   
71                    0       2       0   7.74   177049.0   1013.0   
72                    0       2       1   8.14   133639.0    385.0   
73                    0       2       0   8.02   115427.0    536.0   
75                    0       0       1   7.35    10912.0   2286.0   
76                    0       0       1   7.48    32683.0   1741.0   
77                    0       0       1   8.05    26706.0    499.0   
79                    0       4       3   7.21   101261.0   2835.0   
80                    0       0       1   7.85    31375.0    804.0   
81                    2       0       1   8.09    26728.0    458.0   
82                    2       0       1   7.88    17659.0    742.0   
83                    1      

Myanimelist Anime Data

score_study_df = pd.merge(myAnime_df[["score_diff", "score", "my_score"]], MAL_df_unprocessed["name"], on='series_animedb_id')
score_study_df = score_study_df[score_study_df["my_score"]>0]
print("score_diff mean: ",round(score_study_df["score_diff"].mean(), 4))
print("score mean: ", round(score_study_df["score"].mean(), 2))
print("All Anime score mean: ", round(MAL_df["score"].mean(), 2))

score_study_df = score_study_df[score_study_df["score_diff"]<0]
score_study_df.sort_values("my_score", ascending=True)

ax = plt.gca()
score_study_df[-10:].plot(kind='bar',x='name',y='my_score',color='green', ax=ax)
#score_study_df[-10:].plot(kind='bar',x='name',y='score',color='#2e51a2', ax=ax)
#score_study_df.groupby(['my_score','name']).size().unstack().plot(kind='bar',stacked=True,legend=False)
#plt.savefig('outputfile.svg')

In [37]:
#pd.merge(myAnime_df[["members"]], myAnime_df["popularity"], on='series_animedb_id').sort_values("members", ascending=False)

myAnime_df[["members", "favorites", "popularity"]]
#myAnime_df[["members"]]

members  favorites  popularity
series_animedb_id                                  
1                   795733.0    43460.0        39.0
6                   408548.0    10432.0       146.0
16                  172274.0     3752.0       536.0
19                  394387.0    19188.0       156.0
20                 1091313.0    39356.0        10.0
21                  803871.0    76869.0        36.0
30                  715531.0    45828.0        50.0
33                  325769.0    13782.0       222.0
43                  364643.0     8400.0       177.0
44                  180923.0     4986.0       504.0
50                  117198.0     1035.0       824.0
53                   81572.0      415.0      1139.0
58                   54058.0      360.0      1586.0
60                  172946.0     1946.0       530.0
64                  154546.0     1929.0       610.0
79                  202630.0     1503.0       433.0
101                 224570.0     2584.0       381.0
119                  28858.0       45.0      2362.0
120                 310675.0     7892.0       244.0
121                 854022.0    22764.0        27.0
122                  74904.0     1628.0      1241.0
125                  28139.0       19.0      2389.0
126                  25668.0       64.0      2520.0
145                 131698.0     1611.0       727.0
146                  48458.0      171.0      1709.0
157                 101540.0      572.0       952.0
160                  81980.0      838.0      1128.0
164                 568463.0    11828.0        79.0
169                 114297.0      590.0       846.0
174                 131441.0      599.0       728.0
175                  21984.0       38.0      2761.0
177                 166918.0     2148.0       553.0
189                 191811.0     1470.0       473.0
190                  69568.0       87.0      1321.0
194                  28670.0      108.0      2372.0
195                 123941.0      828.0       779.0
196                  68816.0      172.0      1337.0
199                 789004.0    17043.0        40.0
202                 221781.0     5064.0       386.0
205                 602539.0    21300.0        68.0
226                 901294.0    20990.0        18.0
227                 449437.0    17570.0       122.0
228                 232764.0     2955.0       357.0
232                 255161.0    10388.0       318.0
235                 172217.0     8564.0       537.0
237                 324904.0     8324.0       224.0
241                 105109.0      297.0       934.0
246                  71413.0      359.0      1286.0
269                 889504.0    42878.0        22.0
270                 424367.0     5062.0       134.0
272                  81480.0      763.0      1140.0
275                  17391.0       16.0      3101.0
276                  46023.0      181.0      1772.0
284                   9708.0       55.0      4028.0
299                  27684.0       36.0      2409.0
306                  60981.0      280.0      1463.0
310                   1411.0        2.0      8098.0
322                 112741.0     2151.0       862.0
329                 150440.0     3033.0       625.0
330                 114081.0      531.0       847.0
343                  55868.0      267.0      1545.0
345                  33631.0      217.0      2155.0
355                 384800.0     5249.0       166.0
356                 542280.0     6098.0        86.0
357                 144773.0      643.0       647.0
366                  22432.0       44.0      2724.0
372                  79924.0     1598.0      1163.0
382                  24853.0       34.0      2563.0
384                 226727.0     2034.0       372.0
390                  84848.0      645.0      1095.0
412                  64169.0      134.0      1417.0
431                 535005.0    10846.0        87.0
433                 143928.0      682.0       651.0
437                 210706.0     4579.0       409.0
440                 115103.0     4946.0       839.0
469              

In [38]:
myAnime_df[myAnime_df["my_score"]>0].drop(columns=["my_score"])

type  source  duration  rating  score  scored_by     rank  \
series_animedb_id                                                              
1                     0       0         0       0   8.81   405664.0     26.0   
6                     0       1         0       1   8.30   212537.0    255.0   
30                    0       0         0       1   8.33   402215.0    215.0   
50                    0       1         0       1   7.42    59169.0   1949.0   
79                    0       4         3       3   7.21   101261.0   2835.0   
101                   0       4         0       1   7.41   120702.0   1994.0   
122                   0       1         0       1   8.04    32470.0    508.0   
157                   0       1         3       1   7.06    47384.0   3437.0   
189                   0       1         3       1   7.23   104267.0   2739.0   
199                   1       0        29       2   8.91   550969.0     18.0   
226                   0       1         2       3   7.72   549257.0   1067.0   
227                   2       0         2       1   8.07   252437.0    477.0   
276                   0       1         0       3   7.25    20564.0   2668.0   
330                   0       1         0       3   7.38    64075.0   2155.0   
343                   0       1         0       1   7.09    21830.0   3337.0   
355                   0       2         0       1   7.63   190060.0   1294.0   
357                   2       2         2       0   6.73    83658.0   4749.0   
382                   2       1        26       3   6.47    13103.0   5903.0   
384                   0       1         6       3   7.17   116369.0   2987.0   
390                   0       1         3       1   7.31    41093.0   2445.0   
412                   0       1         0       3   6.63    32523.0   5220.0   
469                   0       1         3       1   7.27    68637.0   2579.0   
482                   0       1         3       1   7.23    65845.0   2757.0   
509                   0       0         2       1   6.88    15751.0   4096.0   
587                   0       2         0       1   7.61    39958.0   1336.0   
777                   2       1       107       0   8.51   243692.0     99.0   
849                   0       2         3       1   7.97   322527.0    610.0   
853                   0       1         3       1   8.32   354874.0    225.0   
880                   0       1         0       1   7.65    27626.0   1226.0   
889                   0       1         0       0   8.12   251420.0    412.0   
910                   0       0         0       1   6.40     5954.0   6188.0   
918                   0       1         0       1   9.00   155333.0     13.0   
940                   0       2         3       1   7.34    23583.0   2312.0   
1066                  3       6        88       1   7.18    16098.0   2971.0   
1067                  0       4         2       0   6.64    10906.0   5168.0   
1195                  0       2         3       1   7.51   292437.0   1655.0   
1210                  0       5         0       3   8.37   202628.0    194.0   
1250                  0       1         0       1   7.38    35622.0   2148.0   
1519                  0       1         0       0   8.25   176872.0    284.0   
1546                  0       1         3       1   7.13    24365.0   3161.0   
1568                  0       1         0       1   7.01    17351.0   3650.0   
1569                  0       4         0       1   7.13    21566.0   3164.0   
1575                  0       0         0       0   8.77   681621.0     32.0   
1581                  0       4         0       1   6.72    11364.0   4800.0   
1689                  1       0         6       1   7.91   303519.0    682.0   
1691                  0       2         0       1   7.42   154407.0   1969.0   
1698                  0       1         6       1   8.39    92020.0    178.0   
1721                  0       1         3       1   6.84     6172.0   4250.0   
1722               

In [67]:
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
scaler = MinMaxScaler()

test_train_div = 0.2


def prepareXy(df):
    X = df[df["my_score"]>0].drop(columns=["my_score", "duration"])
    y = df[df["my_score"]>0].drop(columns=["duration"])["my_score"].tolist()
    
    scaler.fit(X)

    X = scaler.transform(X)
    return X, y

X, y = prepareXy(myAnime_df)

X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=test_train_div, random_state=42)

clf = KNeighborsClassifier(n_neighbors=3, weights="distance")
clf.fit(X, y)
#clf.fit(X_train, y_train)


ModelName = f"Knn-model-Anime-{myinfo['user_name']}-U-{myinfo['user_id']}-id-{myinfo['user_total_anime']}-len-{time.time()}.pkl"
ModelFileLoc = open(f"models/Knn/{ModelName}", "wb")
pickle.dump(clf, ModelFileLoc)
ModelFileLoc.close()

scaler.fit(MAL_df)
X_pred = scaler.transform(MAL_df)

pred = clf.predict(X_pred)
pred_prob = clf.predict_proba(X_pred)
pred_prob = [round(max(i)*100, 2) for i in pred_prob]


# Crerate a prediction df dataset
newMALdf = prepareMALdf("Anime.csv")
for (i, k) in zip(newMALdf["genre"].tolist(), newMALdf.index.tolist()):
        try:
            i = eval(i)
        except:
            continue
        if "Hentai" in i:
            newMALdf = newMALdf.drop(k)
            
for f in statuses_keys["preddfCols"]:
    newMALdf[f] = "Unlabeled"
    for (i, k) in zip(statuses_keys["preddfCols"][f], statuses_keys["keys"]):
        newMALdf.loc[k, f] = i
pred_df = newMALdf
pred_df["score"] = MAL_df["score"]
pred_df["predicted"] = pred
pred_df["confidence %"] = pred_prob
pred_df["my_score"]=0
for s in myAnime_df["my_score"].keys().tolist():
    pred_df.loc[s, "my_score"] = myAnime_df["my_score"][s]
    
pred_df["diff"] = pred_df["my_score"] - pred_df["predicted"]

print(f"Mean scored difference: ", round(pred_df[pred_df["my_score"]>0]["diff"].mean(), 4))
print(f"Mean scored predicted: ", round(pred_df[pred_df["my_score"]>0]["predicted"].mean(), 4))
print(f"Mean predicted: ", round(pred_df["predicted"].mean(), 4))
print(f"My_score mean: ", round(pred_df[pred_df["my_score"]>0]["my_score"].mean(), 4))
print(f"condifence % mean: ", round(pred_df[pred_df["my_score"]>0]["confidence %"].mean(), 4))

pred_df

Mean scored difference:  -0.0179
Mean scored predicted:  7.5856
Mean predicted:  6.8851
My_score mean:  7.5677
condifence % mean:  75.1936


name  \
series_animedb_id                                                      
1                                                       Cowboy Bebop   
5                                    Cowboy Bebop: Tengoku no Tobira   
6                                                             Trigun   
7                                                 Witch Hunter Robin   
8                                                     Bouken Ou Beet   
16                                              Hachimitsu to Clover   
17                                        Hungry Heart: Wild Striker   
18                                            Initial D Fourth Stage   
19                                                           Monster   
20                                                            Naruto   
21                                                         One Piece   
22                                               Tennis no Ouji-sama   
23                                                  Ring ni Kakero 1   
25                                                         Sunabouzu   
26                                                        Texhnolyze   
27                                                     Trinity Blood   
28                                                  Yakitate!! Japan   
29                                                            Zipang   
30                                           Neon Genesis Evangelion   
31                          Neon Genesis Evangelion: Death & Rebirth   
32                    Neon Genesis Evangelion: The End of Evangelion   
33                                              Kenpuu Denki Berserk   
43                                                Ghost in the Shell   
44                 Rurouni Kenshin: Meiji Kenkaku Romantan - Tsui...   
45                           Rurouni Kenshin: Meiji Kenkaku Romantan   
46                 Rurouni Kenshin: Meiji Kenkaku Romantan - Ishi...   
47                                                             Akira   
48                                                       .hack//Sign   
50                                             Aa! Megami-sama! (TV)   
51                                                  Tenshi Kinryouku   
53                                                     Ai Yori Aoshi   
54                                                 Appleseed (Movie)   
55                                                       Arc the Lad   
56                                                           Avenger   
57                                                              Beck   
58                                                       Blue Gender   
59                                                           Chobits   
60                                                     Chrno Crusade   
61                                                         D.N.Angel   
62                                                     D.C.: Da Capo   
63                                                             DearS   
64                                                      Rozen Maiden   
65                                            Rozen Maiden: Träumend   
67                                       Basilisk: Kouga Ninpou Chou   
69                                                      Cluster Edge   
71                                                 Full Metal Panic!   
72                                         Full Metal Panic? Fumoffu   
73                                 Full Metal Panic! The Second Raid   
75                                 Soukyuu no Fafner: Dead Aggressor   
76                                       Mahou Shoujo Lyrical Nanoha   
77                                   Mahou Shoujo Lyrical Nanoha A's   
79                                                          Shuffle!   
80                                                Mobile Suit Gundam   
81                              Mobile Suit Gundam: The 08th MS Team   
82                        Mobile

In [40]:
Acceptable_loss_difference=1
Accuracy_accepted_scores = pred_df[pred_df["my_score"]>0][abs(pred_df['diff'])<=Acceptable_loss_difference].sort_values('diff',
                                                                                                 ascending=False)
__a = len(Accuracy_accepted_scores)
__b = pred_df[pred_df["my_score"]>0].shape[0]
print(f"Acceptable: {__a}/{__b}")
print(f"Acceptable predictions: {round((__a/__b)*100, 3)}%")
pred_df[pred_df["my_score"]>0][abs(pred_df["diff"])>0][["name",
                                                             "score",
                                                             "diff",
                                                             "my_score",
                                                             "predicted",
                                                              "confidence %",
                                                             "genre"]].sort_values(["confidence %"],ascending=True)

Acceptable: 600/613
Acceptable predictions: 97.879%


c:\users\gift\appdata\local\programs\python\python36-32\lib\site-packages\ipykernel_launcher.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  
c:\users\gift\appdata\local\programs\python\python36-32\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  


name  score  \
series_animedb_id                                                             
10155                                                       Dog Days   7.12   
11179                                   Papa no Iukoto wo Kikinasai!   7.43   
31448              Mahouka Koukou no Rettousei: Yoku Wakaru Mahou...   6.55   
11783                                                      Dog Days'   7.23   
16099                            Sword Art Online: Sword Art Offline   6.35   
28063                      Sword Art Online II: Sword Art Offline II   6.72   
28603              Shakugan no Shana: Naze Nani Shana! Nandemo Sh...   6.37   
17875                               Papa no Iukoto wo Kikinasai! OVA   7.44   
6098                                                Sora no Manimani   7.14   
17551              Shakugan no Shana: Shana & Yuuji no Naze Nani ...   6.53   
10119                                        Seitokai Yakuindomo OVA   7.86   
509                                         I My Me! Strawberry Eggs   6.88   
35000              To LOVE-Ru: Multiplication - Mae kara Ushiro kara   7.27   
12729                                            High School DxD OVA   7.43   
1815                                         Shakugan no Shana Movie   7.43   
23847              Yahari Ore no Seishun Love Comedy wa Machigatt...   8.28   
20847                                           Seitokai Yakuindomo*   7.81   
4063                                                         Sekirei   7.30   
18053               Koi to Senkyo to Chocolate: Ikenai Hazuki-sensei   6.85   
18753              Yahari Ore no Seishun Love Comedy wa Machigatt...   7.63   
10209                                    Kore wa Zombie Desu ka? OVA   7.51   
2026                                               Hayate no Gotoku!   7.68   
2926                                                Myself; Yourself   7.32   
30279                                             Yuru Yuri San☆Hai!   8.02   
12291                                              Acchi Kocchi (TV)   7.60   
34403                                                Hajimete no Gal   6.50   
16706                           Kami nomi zo Shiru Sekai: Megami-hen   8.20   
30885                                           Noragami Aragoto OVA   8.07   
23153                                          Hayate no Gotoku! OVA   7.22   
1519                                Black Lagoon: The Second Barrage   8.25   
14513                                   Magi: The Labyrinth of Magic   8.20   
880                            Aa! Megami-sama!: Sorezore no Tsubasa   7.65   
14713                                         Kamisama Hajimemashita   8.13   
8769                     Ore no Imouto ga Konnani Kawaii Wake ga Nai   7.30   
28221                                                        Etotama   6.96   
31380                                    To LOVE-Ru Darkness 2nd OVA   7.74   
20359                                 Yamada-kun to 7-nin no Majo PV   7.39   
3712                           Zero no Tsukaima: Princesses no Rondo   7.54   
12823                         Shakugan no Shana III (Final) Specials   7.19   
3470                                                       Special A   7.70   
31298              Baka to Test to Shoukanjuu: Matsuri - Sentakus...   7.17   
13663                                            To LOVE-Ru Darkness   7.68   
14957              Shakugan no Shana: Friagne to Marianne no Naze...   6.62   
33173                                         Sansha Sanyou Specials   6.74   
10521                                                     Working'!!   7.95   
4744                                         Akaneiro ni Somaru Saka   6.59   

                   diff  my_score  predicted  confidence %  \
series_animedb_id                                            
10155                 1         8          7         34.08   
11179                 3         8          5         35.73   
31448                -2

In [68]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression

tfidf = TfidfVectorizer(sublinear_tf=True, min_df=5, norm='l2', encoding='latin-1', ngram_range=(1, 2), stop_words='english')
X_syn = tfidf.fit_transform(filldfna(newMALdf[newMALdf["my_score"]>0])["synopsis"]).toarray()
y_syn = newMALdf[newMALdf["my_score"]>0]["my_score"]

start_time = time.time()
clf_syn = LogisticRegression(random_state=0, solver='lbfgs',
                         multi_class='multinomial').fit(X_syn, y_syn)
print(f"Fitted LR in {round(time.time()-start_time, 2)}s")

ModelName = f"LogisticRegression-model-Anime-{myinfo['user_name']}-U-{myinfo['user_id']}-id-{myinfo['user_total_anime']}-len-{time.time()}.pkl"
ModelFileLoc = open(f"models/LogisticRegression/{ModelName}", "wb")
pickle.dump(clf_syn, ModelFileLoc)
ModelFileLoc.close()

syn_pred = clf_syn.predict(tfidf.transform(filldfna(newMALdf)["synopsis"]))
syn_pred_proba = clf_syn.predict_proba(tfidf.transform(filldfna(newMALdf)["synopsis"]))
synclf_score = clf_syn.score(tfidf.transform(filldfna(newMALdf[newMALdf["my_score"]>0])["synopsis"]),
              newMALdf[newMALdf["my_score"]>0]["my_score"])
print(f"{round(synclf_score*100, 2)}%")

pred_df["predicted synopis"] = syn_pred
syn_pred_proba = [round(max(i)*100, 2) for i in syn_pred_proba]
pred_df["confidence % synopis"] = syn_pred_proba
pred_df["diff synopis"] = pred_df["my_score"] - pred_df["predicted synopis"]
pred_df["diff models"] = pred_df["diff"] - pred_df["diff synopis"]
pred_df["score Avg. Pred."] = (pred_df["predicted"] + pred_df["predicted synopis"]) / 2
pred_df["score Avg. Pred. W(3:1)"] = round((pred_df["predicted"]*3 + 
                                            pred_df["predicted synopis"]) / (3 + 1),0)
pred_df["confidence % Avg."] = round((pred_df["confidence %"] + 
                                      pred_df["confidence % synopis"]) / 2,2)
pred_df["confidence % synopis Avg. W(3:1)"] = round((pred_df["confidence %"]*3 + 
                                                     pred_df["confidence % synopis"]) / (3 + 1), 2)
pred_df["diff Avg."] = pred_df["my_score"] - pred_df["score Avg. Pred."]
pred_df["diff confidence"] = pred_df["confidence % Avg."] - pred_df["confidence % synopis Avg. W(3:1)"]
pred_df["diff Avg. W(3:1)"] = pred_df["my_score"] - pred_df["score Avg. Pred. W(3:1)"]
print(f"diff Avg. mean: {pred_df[pred_df['my_score']>0]['diff Avg.'].mean()}")
print(f"diff Avg. W(3:1) mean: {pred_df[pred_df['my_score']>0]['diff Avg. W(3:1)'].mean()}")
print(f"diff confidence mean: {pred_df[pred_df['my_score']>0]['diff confidence'].mean()}")
pred_df[pred_df["my_score"]>=0][pred_df["my_status"]=="Unlabeled"][["name",
                                                             "score",
                                                             #"diff",
                                                             #"diff synopis",
                                                             "predicted",
                                                            "predicted synopis",
                                                            "confidence % Avg.",
                                                            "confidence % synopis Avg. W(3:1)",
                                                            "score Avg. Pred.",
                                                            "score Avg. Pred. W(3:1)",
                                                            #"diff Avg.",
                                                            #"diff Avg. W(3:1)",
                                                            "diff confidence",
                                                            "my_score",
                                                             "genre",
                                                            "synopsis"]].sort_values(["score Avg. Pred. W(3:1)"],ascending=True)

Fitted LR in 0.22s
71.94%
diff Avg. mean: -0.132952691680261
diff Avg. W(3:1) mean: -0.0636215334420881
diff confidence mean: -7.914991843393148


name  score  \
series_animedb_id                                                             
36840                                          25-sai no Joshikousei   5.58   
15377                                  Hyakka Ryouran: Samurai Bride   6.86   
11525                                               Mamimume★Mogacho   5.68   
20237                             Anime Document: München e no Michi   5.55   
17379              Street Fighter II: Yomigaeru Fujiwara-Kyou - T...   6.10   
23325                                  Shirogane no Ishi: Argevollen   6.53   
8678                            Sangokushi II: Amakakeru Otoko-tachi   6.65   
10563               Yakyuukyou no Uta: Kita no Ookami Minami no Tora   6.44   
17353                                            Tenpou Suikoden Neo   4.88   
20383                          Baka Mukashibanashi Movie: Jijii Wars   5.37   
21821                                         Fuuun Ishin Dai☆Shogun   5.79   
29850                                            AKB48 Stage Fighter   5.27   
4440                                                Sugata Sanshirou   6.70   
36978                                                Annyeong Totobi   3.43   
36981                                           Neko no Dayan (2017)   6.78   
5814                                 Dankichi-jima no Olympic Taikai   4.28   
38131                              Zhu Zhu Xia: Chao Xing Meng Chong   4.14   
35799                                                      Miniforce   4.00   
8644                                              Sylvanian Families   5.77   
4462                                 Tairiki Tarou no Mucha Shuugyou   4.70   
5838                                        Furudera no Obake-soudou   4.98   
38180              Heavy Object: Dai 37 Kidou Seihi Daitai - Saku...   6.16   
33583                                                      Nana Moon   6.36   
5813                                           Urashima Tarou (1931)   4.52   
36883                                                  Wares: Beyond   4.35   
5872                                     Doubutsu Mura no Sports Day   5.02   
27459                                         Porong Porong Pororo 5   5.47   
27457                                         Porong Porong Pororo 4   5.25   
5871                              Norakuro Nitouhei: Kyouren no Maki   4.95   
2876                                                Hoshi no Orpheus   5.38   
5870                                               Hibari no Yadogae   4.87   
4332                               Seigi wo Aisuru Mono Gekkou Kamen   6.81   
10554                                              Yakyuukyou no Uta   6.62   
5869                                                  Chou no Sainan   5.29   
24441                                                   Shiden Pilot   4.77   
27451                                         Porong Porong Pororo 2   5.53   
16261                                                Arisa☆Good Luck   5.72   
23349                                         Kirin Monoshiri Yakata   6.04   
35848                                                        Promare  -1.00   
2181                                                TANK S.W.A.T. 01   5.07   
36937                                 Virtua Fighter: Costomize Clip   6.15   
17395                                                         Ark IX   5.22   
32385                                                    Project HAL   5.82   
5812                                            Doubutsu Sumo Taikai   4.60   
36996                                                  Jian Wangchao   6.18   
5811                                               Nezumi no Rusuban   4.51   
2765                                       Momotarou: Umi no Shinpei   5.30   
4553                                         Sukima no Kuni no Polta   5.44   
33484                                                     Shiroi Zou   5.41   
38069                              

In [56]:
pred_df

name  \
series_animedb_id                                                      
1                                                       Cowboy Bebop   
5                                    Cowboy Bebop: Tengoku no Tobira   
6                                                             Trigun   
7                                                 Witch Hunter Robin   
8                                                     Bouken Ou Beet   
16                                              Hachimitsu to Clover   
17                                        Hungry Heart: Wild Striker   
18                                            Initial D Fourth Stage   
19                                                           Monster   
20                                                            Naruto   
21                                                         One Piece   
22                                               Tennis no Ouji-sama   
23                                                  Ring ni Kakero 1   
25                                                         Sunabouzu   
26                                                        Texhnolyze   
27                                                     Trinity Blood   
28                                                  Yakitate!! Japan   
29                                                            Zipang   
30                                           Neon Genesis Evangelion   
31                          Neon Genesis Evangelion: Death & Rebirth   
32                    Neon Genesis Evangelion: The End of Evangelion   
33                                              Kenpuu Denki Berserk   
43                                                Ghost in the Shell   
44                 Rurouni Kenshin: Meiji Kenkaku Romantan - Tsui...   
45                           Rurouni Kenshin: Meiji Kenkaku Romantan   
46                 Rurouni Kenshin: Meiji Kenkaku Romantan - Ishi...   
47                                                             Akira   
48                                                       .hack//Sign   
50                                             Aa! Megami-sama! (TV)   
51                                                  Tenshi Kinryouku   
53                                                     Ai Yori Aoshi   
54                                                 Appleseed (Movie)   
55                                                       Arc the Lad   
56                                                           Avenger   
57                                                              Beck   
58                                                       Blue Gender   
59                                                           Chobits   
60                                                     Chrno Crusade   
61                                                         D.N.Angel   
62                                                     D.C.: Da Capo   
63                                                             DearS   
64                                                      Rozen Maiden   
65                                            Rozen Maiden: Träumend   
67                                       Basilisk: Kouga Ninpou Chou   
69                                                      Cluster Edge   
71                                                 Full Metal Panic!   
72                                         Full Metal Panic? Fumoffu   
73                                 Full Metal Panic! The Second Raid   
75                                 Soukyuu no Fafner: Dead Aggressor   
76                                       Mahou Shoujo Lyrical Nanoha   
77                                   Mahou Shoujo Lyrical Nanoha A's   
79                                                          Shuffle!   
80                                                Mobile Suit Gundam   
81                              Mobile Suit Gundam: The 08th MS Team   
82                        Mobile